# Importation

In [ ]:
!pip install -q --upgrade catboost
!pip install -q scikit-learn
!pip install -q --upgrade pycaret

In [ ]:
import math
import random
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
from datetime import datetime, timedelta
import plotly.express as px
import plotly.io as pio
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from google.colab import drive
from pydantic import BaseModel
from pycaret.regression import setup, compare_models
from sklearn.ensemble import IsolationForest
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.feature_selection import SelectKBest, f_regression
from scipy import signal
from catboost import CatBoostRegressor
from xgboost import XGBRegressor
from typing import Dict
from typing_extensions import Annotated
from sklearn.model_selection import GridSearchCV
import joblib



pio.templates.default = "plotly_dark"

In [ ]:
class Config(BaseModel):
    USE_TRAJECTORY: bool = False
    SPLIT_BY_WTC: bool = False
    SPLIT_BY_MTOW: bool = False
    FIND_BEST_MODEL: bool = False
    USE_ENSEMBLE: bool = False
    CATBOOST_MODEL_PATH: str = "/content/drive/MyDrive/PRCModels/catboost_model_{}.pkl"
    XGBOOST_MODEL_PATH: str = "/content/drive/MyDrive/PRCModels/xgboost_model_{}.pkl"


config = Config()

In [ ]:
FLIGHT_PHASES_REFINEMENT = True

# Getting Data

In [ ]:
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# parquet_files = glob.glob('/content/drive/MyDrive/PRC/Data/*.parquet')
parquet_file_path = '/content/drive/MyDrive/PRC/Data/2022-01-01.parquet'
challenge_file_path = '/content/drive/MyDrive/PRC/Data/challenge_set.csv'
submisstion_file_path = '/content/drive/MyDrive/PRC/Data/submission_set.csv'

trajectory_df = pd.read_parquet(parquet_file_path) # Parquet stores dtype by default
trajectory_df = trajectory_df[:len(trajectory_df)]#//10]  # Small data for the baseline
train_df = pd.read_csv(challenge_file_path, parse_dates=['date', 'actual_offblock_time', 'arrival_time'])
test_df = pd.read_csv(submisstion_file_path, parse_dates=['date', 'actual_offblock_time', 'arrival_time']).drop(["tow"], axis=1)

In [ ]:
trajectory_df.tail(3)

flight_id                 timestamp  latitude  longitude  altitude  \
5909616  248772010 2022-01-02 01:59:57+00:00  44.06575 -58.601074   40975.0   
5909617  248772010 2022-01-02 01:59:58+00:00  44.06575 -58.601074   40975.0   
5909618  248772010 2022-01-02 01:59:59+00:00  44.06575 -58.601074   40975.0   

         groundspeed      track  vertical_rate  u_component_of_wind  \
5909616        543.0  76.040526          -64.0            49.665905   
5909617        543.0  76.040526          -64.0            49.665890   
5909618        543.0  76.040526          -64.0            49.665875   

         v_component_of_wind  temperature  specific_humidity     icao24  
5909616           -31.158336   210.208643           0.000013  248772010  
5909617           -31.158134   210.208632           0.000013  248772010  
5909618           -31.157932   210.208621           0.000013  248772010

In [ ]:
trajectory_df.sort_values("altitude").head()

flight_id                 timestamp   latitude  longitude  altitude  \
4976611  248753716 2022-01-01 08:43:57+00:00  50.600886   5.941080   -1000.0   
3994953  248757164 2022-01-01 20:19:19+00:00  42.919441  23.025970    -825.0   
4075988  248765597 2022-01-01 15:02:22+00:00  40.093441  -2.839466    -800.0   
886139   248764524 2022-01-01 11:30:58+00:00  48.489928   2.258124    -800.0   
2741367  248765281 2022-01-01 08:24:33+00:00  50.893443   4.499359    -800.0   

         groundspeed       track  vertical_rate  u_component_of_wind  \
4976611        405.0  298.587902        -3008.0            -4.676256   
3994953        448.0  107.544832            0.0             1.886192   
4075988        433.0  191.854602            0.0             0.476404   
886139         412.0  197.818889            0.0            -4.016883   
2741367        118.0  249.727314         -640.0             0.865356   

         v_component_of_wind  temperature  specific_humidity     icao24  
4976611             1.139285   285.208894           0.007699  248753716  
3994953            -0.520333   285.600480           0.005527  248757164  
4075988             0.213125   296.964754           0.005604  248765597  
886139              2.499475   279.057464           0.008910  248764524  
2741367            11.374119   282.421174           0.008033  248765281

In [ ]:
trajectory_df.flight_id.nunique(), trajectory_df.shape

(790, (5909619, 13))

In [ ]:
train_df.head(3)

flight_id       date                          callsign  adep  \
0  248763780 2022-01-01  3840d84f25d3f5fcc0a1be3076bb4039  EGLL   
1  248760618 2022-01-01  f6f610e73002b8892a239a81321f7f1d  LEBL   
2  248753824 2022-01-01  139670936660762c230ca92556ba842b  ESSA   

           name_adep country_code_adep  ades       name_ades  \
0    London Heathrow                GB  EICK            Cork   
1          Barcelona                ES  KMIA           Miami   
2  Stockholm Arlanda                SE  KORD  Chicago O'Hare   

  country_code_ades      actual_offblock_time              arrival_time  \
0                IE 2022-01-01 13:46:00+00:00 2022-01-01 15:04:56+00:00   
1                US 2022-01-01 09:55:00+00:00 2022-01-01 19:37:56+00:00   
2                US 2022-01-01 09:39:00+00:00 2022-01-01 19:08:13+00:00   

  aircraft_type wtc                           airline  flight_duration  \
0          A320   M  a73f82288988b79be490c6322f4c32ed               61   
1          B772   H  5543e4dc327359ffaf5b9c0e6faaf0e1              570   
2          A333   H  8be5c854fd664bcb97fb543339f74770              554   

   taxiout_time  flown_distance       tow  
0            18             321   54748.0  
1            13            4193  185441.0  
2            15            3770  230396.0

In [ ]:
train_df.flight_id.nunique(), train_df.aircraft_type.nunique()

(369013, 30)

In [ ]:
test_df.head(3)

flight_id       date                          callsign  adep  \
0  248753821 2022-01-01  3b3de0f3ad0ee192513995c02f7bf7cf  LTFJ   
1  248753822 2022-01-01  e06dd03d4a879ca37d9e18c1bd7cad16  EBBR   
2  248754498 2022-01-01  2d3b1c962c78c4ebeef11bcd51b9e94c  KMIA   

                name_adep country_code_adep  ades        name_ades  \
0  Istanbul Sabiha Gokcen                TR  LFLL             Lyon   
1                Brussels                BE  KJFK     New York JFK   
2                   Miami                US  EGLL  London Heathrow   

  country_code_ades      actual_offblock_time              arrival_time  \
0                FR 2022-01-01 09:44:00+00:00 2022-01-01 12:48:33+00:00   
1                US 2022-01-01 09:45:00+00:00 2022-01-01 17:49:51+00:00   
2                GB 2022-01-01 01:52:00+00:00 2022-01-01 09:55:16+00:00   

  aircraft_type wtc                           airline  flight_duration  \
0          B738   M  6351ec1b849adacc0cbb3b1313d8d39b              170   
1          A333   H  bdeeef3a675587d530de70a25d7118d2              470   
2          B77W   H  5543e4dc327359ffaf5b9c0e6faaf0e1              473   

   taxiout_time  flown_distance  
0            15            1122  
1            15            3205  
2            10            3965

In [ ]:
train_df.shape, test_df.shape

((369013, 18), (105959, 17))

In [ ]:
test_df.aircraft_type.unique()

array(['B738', 'A333', 'B77W', 'B38M', 'A320', 'E190', 'CRJ9', 'A21N',
       'B789', 'A20N', 'B739', 'BCS3', 'E195', 'A321', 'A359', 'A319',
       'A332', 'B788', 'BCS1', 'B763', 'AT76', 'B772', 'B737', 'A343',
       'B39M', 'B752', 'B773', 'E290'], dtype=object)

# EDA

## Understanding the Flight Metadata

### Examine the shape of the datasets

In [ ]:
print("Train Flights Shape:", train_df.shape)
print("Test Flights Shape:", test_df.shape)

Train Flights Shape: (369013, 18)
Test Flights Shape: (105959, 17)


### Summary statistics

In [ ]:
train_df.describe()

flight_id                           date  flight_duration  \
count  3.690130e+05                         369013    369013.000000   
mean   2.535220e+08  2022-07-14 06:48:45.496933632       145.876779   
min    2.487506e+08            2022-01-01 00:00:00         8.000000   
25%    2.512296e+08            2022-04-29 00:00:00        59.000000   
50%    2.536200e+08            2022-07-20 00:00:00       100.000000   
75%    2.559059e+08            2022-10-04 00:00:00       164.000000   
max    2.580745e+08            2022-12-31 00:00:00      1013.000000   
std    2.688565e+06                            NaN       139.337587   

        taxiout_time  flown_distance            tow  
count  369013.000000   369013.000000  369013.000000  
mean       13.489709     1021.728581   79482.257229  
min         0.000000       19.000000   14944.000000  
25%        10.000000      338.000000   55836.000000  
50%        12.000000      647.000000   63852.000000  
75%        16.000000     1113.000000   73756.000000  
max        90.000000     7272.000000  351327.000000  
std         5.779555     1128.171163   53250.919631

In [ ]:
train_df.describe()

flight_id                           date  flight_duration  \
count  3.690130e+05                         369013    369013.000000   
mean   2.535220e+08  2022-07-14 06:48:45.496933632       145.876779   
min    2.487506e+08            2022-01-01 00:00:00         8.000000   
25%    2.512296e+08            2022-04-29 00:00:00        59.000000   
50%    2.536200e+08            2022-07-20 00:00:00       100.000000   
75%    2.559059e+08            2022-10-04 00:00:00       164.000000   
max    2.580745e+08            2022-12-31 00:00:00      1013.000000   
std    2.688565e+06                            NaN       139.337587   

        taxiout_time  flown_distance            tow  
count  369013.000000   369013.000000  369013.000000  
mean       13.489709     1021.728581   79482.257229  
min         0.000000       19.000000   14944.000000  
25%        10.000000      338.000000   55836.000000  
50%        12.000000      647.000000   63852.000000  
75%        16.000000     1113.000000   73756.000000  
max        90.000000     7272.000000  351327.000000  
std         5.779555     1128.171163   53250.919631

### Missing Values

In [ ]:
train_df.isnull().sum()

flight_id               0
date                    0
callsign                0
adep                    0
name_adep               0
country_code_adep       0
ades                    0
name_ades               0
country_code_ades       0
actual_offblock_time    0
arrival_time            0
aircraft_type           0
wtc                     0
airline                 0
flight_duration         0
taxiout_time            0
flown_distance          0
tow                     0
dtype: int64

In [ ]:
test_df.isnull().sum()

flight_id               0
date                    0
callsign                0
adep                    0
name_adep               0
country_code_adep       0
ades                    0
name_ades               0
country_code_ades       0
actual_offblock_time    0
arrival_time            0
aircraft_type           0
wtc                     0
airline                 0
flight_duration         0
taxiout_time            0
flown_distance          0
dtype: int64

### TOW Histogram

In [ ]:
fig = px.histogram(train_df['tow'], title="Distribution of TakeOff Weight (TOW)")
fig.update_xaxes(title_text='TakeOff Weight (kg)')
fig.update_yaxes(title_text='Frequency')
fig.show()

### Correlation Matrix

In [ ]:
corr_matrix = train_df.select_dtypes(include=[np.number]).corr()
fig = px.imshow(corr_matrix, title='Correlation Matrix')
fig.show()

### Does any flight in the test not belong in the trajectory?

In [ ]:
test_flight_ids = set(test_df['flight_id'])
trajectory_flight_ids = set(trajectory_df['flight_id'])

missing_flight_ids = test_flight_ids - trajectory_flight_ids

if missing_flight_ids:
    print(f"There are {len(missing_flight_ids)} flight IDs in the test data that don't appear in the trajectory data:")
    print(missing_flight_ids)
else:
    print("All flight IDs in the test data are present in the trajectory data.")

There are 105775 flight IDs in the test data that don't appear in the trajectory data:
{252444678, 251396103, 257687558, 255590411, 248774668, 254803980, 249036815, 252706836, 255066133, 256376854, 257163284, 250609690, 255852571, 251920412, 252182559, 254804000, 255852576, 251658275, 254804004, 249823269, 255328295, 255328300, 257163313, 250085426, 250871860, 256639030, 253755448, 248774714, 250085440, 254804035, 255590469, 250609736, 250871886, 257425488, 254804054, 249823321, 254017627, 255590499, 253493348, 256639080, 250871914, 257687662, 256639089, 250085493, 249561212, 256901245, 257687678, 255066239, 256376960, 255066244, 253755526, 250347656, 250871950, 256639120, 248774806, 254279831, 250871960, 255590558, 257949854, 254279855, 255328432, 257163441, 253493430, 255066298, 256377022, 251396288, 250085572, 251658439, 250872011, 250347726, 252182741, 254542038, 255066325, 257163481, 252707037, 254804189, 251920607, 254279903, 256639198, 250872034, 254279906, 256901345, 248774885,

## Understanding the Trajectory Data

### Number of unique flights in trajectory data

In [ ]:
trajectory_df['flight_id'].nunique()

790

### Missing Value

In [ ]:
trajectory_df.isnull().sum()

flight_id                  0
timestamp                  0
latitude                   0
longitude                  0
altitude                   0
groundspeed            19432
track                  19432
vertical_rate          19432
u_component_of_wind        0
v_component_of_wind        0
temperature                0
specific_humidity          0
icao24                     0
dtype: int64

In [ ]:
print(f"Missing: {trajectory_df.groundspeed.isnull().sum() / trajectory_df.shape[0] * 100:.2f}%")

Missing: 0.33%


Since we have a lot of data, we might consider removing null later.

### Plot sample trajectory

In [ ]:
sample_flight_id = trajectory_df['flight_id'].iloc[0]
sample_flight_data = trajectory_df[trajectory_df['flight_id'] == sample_flight_id]

fig = px.line(sample_flight_data, x='timestamp', y='altitude',
            title=f'Altitude over Time for Flight ID: {sample_flight_id}')
fig.update_xaxes(title_text='Timestamp')
fig.update_yaxes(title_text='Altitude')
fig.show()

There should be some sort of sensor error. (Remove the outlier)

# Data Preprocessing

## Find duration

In [ ]:
def get_duration(df):
    df['actual_offblock_time'] = pd.to_datetime(df['actual_offblock_time'])
    df['arrival_time'] = pd.to_datetime(df['arrival_time'])
    df['duration'] = (df['arrival_time'] - df[
        'actual_offblock_time']).dt.total_seconds() / 60
    return df

train_df = get_duration(train_df)
test_df = get_duration(test_df)

In [ ]:
train_df.head()

flight_id       date                          callsign  adep  \
0  248763780 2022-01-01  3840d84f25d3f5fcc0a1be3076bb4039  EGLL   
1  248760618 2022-01-01  f6f610e73002b8892a239a81321f7f1d  LEBL   
2  248753824 2022-01-01  139670936660762c230ca92556ba842b  ESSA   
3  248753852 2022-01-01  509dc61bb54fbab0e5406067c95603e2  LSZH   
4  248755934 2022-01-01  d0610d000dcf26b1d7bba8103ecc393d  EIDW   

           name_adep country_code_adep  ades        name_ades  \
0    London Heathrow                GB  EICK             Cork   
1          Barcelona                ES  KMIA            Miami   
2  Stockholm Arlanda                SE  KORD   Chicago O'Hare   
3             Zurich                CH  KPHL     Philadelphia   
4             Dublin                IE  EGLL  London Heathrow   

  country_code_ades      actual_offblock_time              arrival_time  \
0                IE 2022-01-01 13:46:00+00:00 2022-01-01 15:04:56+00:00   
1                US 2022-01-01 09:55:00+00:00 2022-01-01 19:37:56+00:00   
2                US 2022-01-01 09:39:00+00:00 2022-01-01 19:08:13+00:00   
3                US 2022-01-01 11:04:00+00:00 2022-01-01 19:32:13+00:00   
4                GB 2022-01-01 12:36:00+00:00 2022-01-01 13:44:32+00:00   

  aircraft_type wtc                           airline  flight_duration  \
0          A320   M  a73f82288988b79be490c6322f4c32ed               61   
1          B772   H  5543e4dc327359ffaf5b9c0e6faaf0e1              570   
2          A333   H  8be5c854fd664bcb97fb543339f74770              554   
3          B788   H  5543e4dc327359ffaf5b9c0e6faaf0e1              497   
4          A21N   M  a73f82288988b79be490c6322f4c32ed               55   

   taxiout_time  flown_distance            tow    duration  
0            18             321   54748.000000   78.933333  
1            13            4193  185441.000000  582.933333  
2            15            3770  230396.000000  569.216667  
3            11            3607  157615.000000  508.216667  
4            14             305   70318.447226   68.533333

## Can we get initial weight for each aircraft_type?

- https://contentzone.eurocontrol.int/aircraftperformance/details.aspx?ICAO=B38M

In [ ]:
external_information = {
  "B738": {
                "MTOW(kg)": 70530,
                "passengers": 162,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 145,
            },
            "A333": {
                "MTOW(kg)": 230000,
                "passengers": 295,
                "ROC_Initial_Climb(ft/min)": 2000,
                "V2 (IAS)": 145,
            },
            "B77W": {
                "MTOW(kg)": 351500,
                "passengers": 365,
                "ROC_Initial_Climb(ft/min)": 2000,
                "V2 (IAS)": 149,
            },
            "B38M": {
                "MTOW(kg)": 82600,
                "passengers": 162,
                "ROC_Initial_Climb(ft/min)": 2500,
                "V2 (IAS)": 145,
            },
            "A320": {
                "MTOW(kg)": 73900,
                "passengers": 150,
                "ROC_Initial_Climb(ft/min)": 2500,
                "V2 (IAS)": 145,
            },
            "E190": {
                "MTOW(kg)": 45995,
                "passengers": 94,
                "ROC_Initial_Climb(ft/min)": 3400,
                "V2 (IAS)": 138,
            },
            "CRJ9": {
                "MTOW(kg)": 38330,
                "passengers": 80,
                "ROC_Initial_Climb(ft/min)": 2500,
                "V2 (IAS)": 140,
            },
            "A21N": {
                "MTOW(kg)": 97000,
                "passengers": 180,
                "ROC_Initial_Climb(ft/min)": 2000,
                "V2 (IAS)": 145,
            },
            "A20N": {
                "MTOW(kg)": 79000,
                "passengers": 150,
                "ROC_Initial_Climb(ft/min)": 2200,
                "V2 (IAS)": 145,
            },
            "B739": {
                "MTOW(kg)": 79015,
                "passengers": 177,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 149,
            },
            "BCS3": {
                "MTOW(kg)": 69900,
                "passengers": 120,
                "ROC_Initial_Climb(ft/min)": 3100,
                "V2 (IAS)": 165,
            },
            "E195": {
                "MTOW(kg)": 52290,
                "passengers": 100,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 140,
            },
            "A321": {
                "MTOW(kg)": 83000,
                "passengers": 185,
                "ROC_Initial_Climb(ft/min)": 2500,
                "V2 (IAS)": 145,
            },
            "A359": {
                "MTOW(kg)": 268000,
                "passengers": 314,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 150,
            },
            "A319": {
                "MTOW(kg)": 64000,
                "passengers": 124,
                "ROC_Initial_Climb(ft/min)": 2500,
                "V2 (IAS)": 135,
            },
            "A332": {
                "MTOW(kg)": 230000,
                "passengers": 253,
                "ROC_Initial_Climb(ft/min)": 2000,
                "V2 (IAS)": 145,
            },
            "B788": {
                "MTOW(kg)": 228000,
                "passengers": 210,
                "ROC_Initial_Climb(ft/min)": 2700,
                "V2 (IAS)": 165,
            },
            "B789": {
                "MTOW(kg)": 253000,
                "passengers": 406,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 165,
            },
            "BCS1": {
                "MTOW(kg)": 63100,
                "passengers": 100,
                "ROC_Initial_Climb(ft/min)": 3500,
                "V2 (IAS)": 140,
            },
            "B763": {
                "MTOW(kg)": 186880,
                "passengers": 269,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 160,
            },
            "AT76": {
                "MTOW(kg)": 23000,
                "passengers": 78,
                "ROC_Initial_Climb(ft/min)": 1350,
                "V2 (IAS)": 116,
            },
            "B772": {
                "MTOW(kg)": 247210,
                "passengers": 305,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 170,
            },
            "B737": {
                "MTOW(kg)": 66320,
                "passengers": 128,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 150,
            },
            "A343": {
                "MTOW(kg)": 275000,
                "passengers": 295,
                "ROC_Initial_Climb(ft/min)": 1400,
                "V2 (IAS)": 145,
            },
            "B39M": {
                "MTOW(kg)": 88300,
                "passengers": 178,
                "ROC_Initial_Climb(ft/min)": 2300,
                "V2 (IAS)": 150,
            },
            "B752": {
                "MTOW(kg)": 115680,
                "passengers": 200,
                "ROC_Initial_Climb(ft/min)": 3500,
                "V2 (IAS)": 145,
            },
            "B773": {
                "MTOW(kg)": 299370,
                "passengers": 368,
                "ROC_Initial_Climb(ft/min)": 3000,
                "V2 (IAS)": 168,
            },
            "E290": {
                "MTOW(kg)": 45995,
                "passengers": 94,
                "ROC_Initial_Climb(ft/min)": 3400,
                "V2 (IAS)": 138,
            },
}

### Make sure it covers all aircraft in the test data. (Not the train data)

In [ ]:
unique_aircraft_types = set(test_df['aircraft_type'].unique())
external_info_keys = set(external_information.keys())

missing_aircraft_types = unique_aircraft_types - external_info_keys
missing_aircraft_types

set()

In [ ]:
external_df = pd.DataFrame.from_dict(external_information, orient='index')
external_df.reset_index(inplace=True)
external_df.rename(columns={'index': 'aircraft_type'}, inplace=True)
external_df.head()

aircraft_type  MTOW(kg)  passengers  ROC_Initial_Climb(ft/min)  V2 (IAS)
0          B738     70530         162                       3000       145
1          A333    230000         295                       2000       145
2          B77W    351500         365                       2000       149
3          B38M     82600         162                       2500       145
4          A320     73900         150                       2500       145

In [ ]:
columns_to_plot = ['MTOW(kg)', 'passengers', 'ROC_Initial_Climb(ft/min)', 'V2 (IAS)']

fig = make_subplots(rows=4, cols=4,
                  shared_xaxes=True, shared_yaxes=True,
                  column_titles=columns_to_plot,
                  row_titles=columns_to_plot)

for i, col1 in enumerate(columns_to_plot):
  for j, col2 in enumerate(columns_to_plot):
      fig.add_trace(
          go.Scatter(
              x=external_df[col2],
              y=external_df[col1],
              mode='markers+text',
              # text=external_df['aircraft_type'],
              textposition='top center',
              name=f'{col1} vs {col2}',
              showlegend=False
          ),
          row=i+1, col=j+1
      )

fig.update_layout(
  title='Relationships Among Aircraft Characteristics',
  height=800,
  width=1000,
  showlegend=False,
)

fig.show()

### Merge external information

In [ ]:
def merge_external_info(df, external_df):
  return pd.merge(df, external_df, on='aircraft_type', how='left')

train_df = merge_external_info(train_df, external_df)
test_df = merge_external_info(test_df, external_df)

### Filter train data to only external information we have

In [ ]:
train_df = train_df[train_df['aircraft_type'].isin(external_information.keys())]
train_df.reset_index(drop=True, inplace=True)
test_df.reset_index(drop=True, inplace=True)
train_df.isnull().sum(), test_df.isnull().sum()

(flight_id                    0
 date                         0
 callsign                     0
 adep                         0
 name_adep                    0
 country_code_adep            0
 ades                         0
 name_ades                    0
 country_code_ades            0
 actual_offblock_time         0
 arrival_time                 0
 aircraft_type                0
 wtc                          0
 airline                      0
 flight_duration              0
 taxiout_time                 0
 flown_distance               0
 tow                          0
 duration                     0
 MTOW(kg)                     0
 passengers                   0
 ROC_Initial_Climb(ft/min)    0
 V2 (IAS)                     0
 dtype: int64,
 flight_id                    0
 date                         0
 callsign                     0
 adep                         0
 name_adep                    0
 country_code_adep            0
 ades                         0
 name_ades               

## Clean df with isolation forest

In [ ]:
def clean_dataframe_with_isolation_forest(df, contamination=0.01):
  print("Shape before clean: ", df.shape)
  cleaned_df = df.copy()
  cleaned_df = cleaned_df.dropna()

  numeric_columns = cleaned_df.select_dtypes(include=[np.number]).columns

  # Standardize the numeric columns
  scaler = StandardScaler()
  scaled_data = scaler.fit_transform(cleaned_df[numeric_columns])

  # Use Isolation Forest for outlier detection
  iso_forest = IsolationForest(contamination=contamination, random_state=42)
  outlier_labels = iso_forest.fit_predict(scaled_data)

  # Keep only the non-outlier data points
  cleaned_df = cleaned_df[outlier_labels == 1].reset_index(drop=True)

  print("Shape after clean: ", cleaned_df.shape)
  return cleaned_df

In [ ]:
def clean_trajectory_with_isolation_forest(df, contamination=0.01):
  print("Shape before clean: ", df.shape)
  cleaned_df = df.copy()

  # Filter rows based on altitude (From the ISA code)
  cleaned_df = cleaned_df[(cleaned_df['altitude'] >= 0) & (cleaned_df['altitude'] <= 47000)]
  cleaned_df = cleaned_df.dropna()

  numeric_columns = cleaned_df.select_dtypes(include=[np.number]).columns

  def clean_group(group):
      if len(group) <= 1:
          return group

      scaler = StandardScaler()
      scaled_data = scaler.fit_transform(group[numeric_columns])

      iso_forest = IsolationForest(contamination=contamination, random_state=42)
      outlier_labels = iso_forest.fit_predict(scaled_data)

      return group[outlier_labels == 1]

  # Apply the cleaning function to each flight_id group
  cleaned_df = cleaned_df.groupby('flight_id').apply(clean_group)

  # Reset index once before returning
  cleaned_df = cleaned_df.reset_index(drop=True)

  print("Shape after clean: ", cleaned_df.shape)
  return cleaned_df

In [ ]:
train_df = clean_dataframe_with_isolation_forest(train_df)
test_df = clean_dataframe_with_isolation_forest(test_df)
# trajectory_df = clean_trajectory_with_isolation_forest(trajectory_df)

Shape before clean:  (369010, 23)
Shape after clean:  (365319, 23)
Shape before clean:  (105959, 22)
Shape after clean:  (104899, 22)


In [ ]:
sample_flight_id = random.choice(trajectory_df['flight_id'].unique())
sample_flight_data = trajectory_df[trajectory_df['flight_id'] == sample_flight_id]

fig = px.line(sample_flight_data, x='timestamp', y='altitude',
            title=f'Altitude over Time for Flight ID: {sample_flight_id}')
fig.update_xaxes(title_text='Timestamp')
fig.update_yaxes(title_text='Altitude')

fig.show()

## Find Thrust - Drag

In [ ]:
g = 32.17405  # Gravitational acceleration (ft/s^2)
kt_to_ft_per_sec = 1.6878098571012  # knots to ft/s
m_to_ft = 3.28084

### Find the standard temperature (ISA)

In [ ]:
def isa(alt):
  T0 = 288.15
  p0 = 101325
  rho0 = 1.225
  a0 = 340.294
  k = 1.4
  R = 287.05287
  betabelow = -0.0065
  trop = 11000

  if alt < 0 or alt > 47000:
      print("Altitude must be in [0, 47000]")
      return None, None

  if alt == 0:
      return T0, rho0

  if 0 < alt <= trop:
      temperature = T0 + betabelow * alt
      pressure = p0 * (temperature / T0) ** ((-1) * g / (betabelow * R))
  elif trop < alt < 47000:
      temperature = T0 + betabelow * trop
      pressure = (p0 * (temperature / T0) ** ((-1) * g / (betabelow * R))) * math.exp(-g * (alt - trop) / (R * temperature))

  density = pressure / (R * temperature)
  return temperature, density

### Find V

In [ ]:
def calculate_true_airspeed(row):
  GS = row['groundspeed']
  track = np.radians(row['track'])
  u_wind = row['u_component_of_wind']
  v_wind = row['v_component_of_wind']

  V = np.sqrt((GS * np.sin(track) - u_wind)**2 + (GS * np.cos(track) - v_wind)**2) * ktstofts
  return V

### Find dh/dt

In [ ]:
def calculate_vertical_speed(row):
  return row['vertical_rate'] / 60  # Convert from ft/min to ft/s

### Find temperature deviation (Δt)

In [ ]:
def calculate_temp_deviation(row):
  isa_temp, _ = isa(row['altitude'])
  return row['temperature'] - isa_temp

### Find horizontal acceleration (dV/dt)

In [ ]:
def calculate_horizontal_acceleration(group):
  group = group.sort_values('timestamp')
  group['V'] = group.apply(calculate_true_airspeed, axis=1)
  group['dV_dt'] = group['V'].diff() / group['timestamp'].diff().dt.total_seconds() # .diff() = current - previous, .diff(-1) = current - next
  return group


### Find wind acceleration (dWi/dt)

In [ ]:
def calculate_wind_acceleration(group):
  group = group.sort_values('timestamp')
  group['W_long'] = (group['u_component_of_wind'] * np.sin(np.radians(group['track'])) +
                     group['v_component_of_wind'] * np.cos(np.radians(group['track']))) * ktstofts
  group['dWi_dt'] = group['W_long'].diff() / group['timestamp'].diff().dt.total_seconds()
  return group

### Segment the Trajectory into Flight Phases
Aggregating the trajectory data by computing averages or maxima over the entire flight might dilute the crucial information specific to the takeoff phase. Since flights consist of multiple phases (takeoff, climb, cruise, descent, landing), combining all phases might mask the effects that are directly influenced by ATOW.

So, we will focus on the `takeoff and initial climb phases`because:

- During takeoff, the aircraft accelerates both horizontally and vertically. This acceleration is directly influenced by the mass.
- Pilots use maximum or near-maximum thrust during takeoff, and any variations in T-D are more likely due to differences in mass rather than throttle settings.
- In cruise, the aircraft's acceleration is minimal, and variations in T-D are more affected by changes in drag due to atmospheric conditions rather than mass.


In [ ]:
def identify_flight_phases(group, flight_phases_refinement=False):
  group = group.sort_values('timestamp').reset_index(drop=True)
  group['altitude_diff'] = group['altitude'].diff()

  # Applies a Savitzky-Golay filter to smooth the altitude profile, reducing noise.
  altitude_smooth = signal.savgol_filter(group['altitude'],
                                         window_length=min(21, len(group) // 2 * 2 + 1),
                                         polyorder=3)

  # Calculate the rate of climb (ROC) (gradient[i] = (f[i+1] - f[i-1]) / (x[i+1] - x[i-1]))
  group['ROC'] = np.gradient(altitude_smooth, group['timestamp'].astype(int) / 10**9)
  max_altitude = group['altitude'].max()
  takeoff_end = group[group['altitude'] > group['altitude'].quantile(0.1)].index[0]
  top_of_climb = group[group['altitude'] > max_altitude * 0.95].index[0]

  takeoff_phase = group.loc[:takeoff_end]
  initial_climb_phase = group.loc[takeoff_end:top_of_climb]
  cruise_phase = group.loc[top_of_climb:]

  if flight_phases_refinement:
    # Refine takeoff phase (focus on the most significant part of the takeoff)
    # The assumption is that the aircraft's weight (ATOW) will have the most significant impact during this high-ROC portion of takeoff.
    takeoff_phase = takeoff_phase[takeoff_phase['ROC'] > takeoff_phase['ROC'].quantile(0.5)]

    # Refine initial climb phase
    initial_climb_phase = initial_climb_phase[
        (initial_climb_phase['ROC'] > initial_climb_phase['ROC'].quantile(0.25)) &
        (initial_climb_phase['altitude'] < max_altitude * 0.8)
    ]

  return takeoff_phase, initial_climb_phase, cruise_phase

### Thrust - Drag (T-D)

In [ ]:
def calculate_thrust_minus_drag_for_phases(trajectory_df):
  td_list = []

  for flight_id, group in tqdm(trajectory_df.groupby('flight_id'), desc="Calculating T-D for each flight"):
      takeoff_phase, initial_climb_phase, _ = identify_flight_phases(group, FLIGHT_PHASES_REFINEMENT)

      # You can combine takeoff and initial climb if desired
      relevant_phase = pd.concat([takeoff_phase, initial_climb_phase])

      if relevant_phase.empty:
          continue

      # Perform calculations only on the relevant phase
      relevant_phase['V'] = relevant_phase.apply(calculate_true_airspeed, axis=1)
      relevant_phase['dh_dt'] = relevant_phase.apply(calculate_vertical_speed, axis=1)
      relevant_phase['delta_t'] = relevant_phase.apply(calculate_temp_deviation, axis=1)

      relevant_phase = calculate_horizontal_acceleration(relevant_phase)
      relevant_phase = calculate_wind_acceleration(relevant_phase)

      # Calculate T - D
      relevant_phase['T_minus_D'] = (
          g * relevant_phase['dh_dt'] / relevant_phase['V'] * (relevant_phase['temperature'] / (relevant_phase['temperature'] - relevant_phase['delta_t']))
          + relevant_phase['dV_dt'] + relevant_phase['dWi_dt']
      )

      # Add flight ID for linking later
      relevant_phase['flight_id'] = flight_id

      # Collect the relevant data
      td_list.append(relevant_phase)

  # Concatenate all flights' data
  td_df = pd.concat(td_list, ignore_index=True)

  # Drop any rows with missing T_minus_D values
  td_df = td_df.dropna(subset=['T_minus_D'])

  return td_df

## Aggregate Features (Still not find the important variables)

In [ ]:
def aggregate_features(td_df):
    numerical_cols = td_df.select_dtypes(include=np.number).columns.tolist()
    if 'flight_id' in numerical_cols:
        numerical_cols.remove('flight_id')
    agg_funcs = {col: ['mean', 'max', 'std'] for col in numerical_cols}
    aggregated_features = td_df.groupby('flight_id').agg(agg_funcs).reset_index()
    aggregated_features.columns = ['_'.join(col).rstrip('_') for col in aggregated_features.columns.values]

    return aggregated_features

## Merging Datasets

In [ ]:
if config.USE_TRAJECTORY:
  td_df = calculate_thrust_minus_drag_for_phases(trajectory_df)
  aggregated_features = aggregate_features(td_df)
  merged_df = pd.merge(train_df, aggregated_features, left_on='flight_id', right_on='flight_id', how='inner')
else:
  merged_df = train_df.copy()
merged_df.head()

flight_id       date                          callsign  adep  \
0  248763780 2022-01-01  3840d84f25d3f5fcc0a1be3076bb4039  EGLL   
1  248760618 2022-01-01  f6f610e73002b8892a239a81321f7f1d  LEBL   
2  248753824 2022-01-01  139670936660762c230ca92556ba842b  ESSA   
3  248753852 2022-01-01  509dc61bb54fbab0e5406067c95603e2  LSZH   
4  248755934 2022-01-01  d0610d000dcf26b1d7bba8103ecc393d  EIDW   

           name_adep country_code_adep  ades        name_ades  \
0    London Heathrow                GB  EICK             Cork   
1          Barcelona                ES  KMIA            Miami   
2  Stockholm Arlanda                SE  KORD   Chicago O'Hare   
3             Zurich                CH  KPHL     Philadelphia   
4             Dublin                IE  EGLL  London Heathrow   

  country_code_ades      actual_offblock_time  ...  \
0                IE 2022-01-01 13:46:00+00:00  ...   
1                US 2022-01-01 09:55:00+00:00  ...   
2                US 2022-01-01 09:39:00+00:00  ...   
3                US 2022-01-01 11:04:00+00:00  ...   
4                GB 2022-01-01 12:36:00+00:00  ...   

                            airline flight_duration taxiout_time  \
0  a73f82288988b79be490c6322f4c32ed              61           18   
1  5543e4dc327359ffaf5b9c0e6faaf0e1             570           13   
2  8be5c854fd664bcb97fb543339f74770             554           15   
3  5543e4dc327359ffaf5b9c0e6faaf0e1             497           11   
4  a73f82288988b79be490c6322f4c32ed              55           14   

  flown_distance            tow    duration  MTOW(kg)  passengers  \
0            321   54748.000000   78.933333   73900.0       150.0   
1           4193  185441.000000  582.933333  247210.0       305.0   
2           3770  230396.000000  569.216667  230000.0       295.0   
3           3607  157615.000000  508.216667  228000.0       210.0   
4            305   70318.447226   68.533333   97000.0       180.0   

   ROC_Initial_Climb(ft/min)  V2 (IAS)  
0                     2500.0     145.0  
1                     3000.0     170.0  
2                     2000.0     145.0  
3                     2700.0     165.0  
4                     2000.0     145.0  

[5 rows x 23 columns]

In [ ]:
merged_df.aircraft_type.nunique(), test_df.aircraft_type.nunique()

(28, 28)

## Normalization

In [ ]:
def normalize_dataframe(df, exclude_columns=None):
    df_normalized = df.copy()

    if exclude_columns is None:
        exclude_columns = []

    columns_to_normalize = df.select_dtypes(include=[np.number]).columns.difference(exclude_columns)
    scaler = StandardScaler()
    df_normalized[columns_to_normalize] = scaler.fit_transform(df[columns_to_normalize])

    return df_normalized

In [ ]:
exclude_cols = ['flight_id', 'tow', 'date', 'callsign', 'adep', 'ades', 'actual_offblock_time', 'arrival_time', 'aircraft_type', 'wtc', 'airline']

norm_df = normalize_dataframe(merged_df, exclude_columns=exclude_cols)
norm_df.head()

flight_id       date                          callsign  adep  \
0  248763780 2022-01-01  3840d84f25d3f5fcc0a1be3076bb4039  EGLL   
1  248760618 2022-01-01  f6f610e73002b8892a239a81321f7f1d  LEBL   
2  248753824 2022-01-01  139670936660762c230ca92556ba842b  ESSA   
3  248753852 2022-01-01  509dc61bb54fbab0e5406067c95603e2  LSZH   
4  248755934 2022-01-01  d0610d000dcf26b1d7bba8103ecc393d  EIDW   

           name_adep country_code_adep  ades        name_ades  \
0    London Heathrow                GB  EICK             Cork   
1          Barcelona                ES  KMIA            Miami   
2  Stockholm Arlanda                SE  KORD   Chicago O'Hare   
3             Zurich                CH  KPHL     Philadelphia   
4             Dublin                IE  EGLL  London Heathrow   

  country_code_ades      actual_offblock_time  ...  \
0                IE 2022-01-01 13:46:00+00:00  ...   
1                US 2022-01-01 09:55:00+00:00  ...   
2                US 2022-01-01 09:39:00+00:00  ...   
3                US 2022-01-01 11:04:00+00:00  ...   
4                GB 2022-01-01 12:36:00+00:00  ...   

                            airline flight_duration taxiout_time  \
0  a73f82288988b79be490c6322f4c32ed       -0.616852     0.793523   
1  5543e4dc327359ffaf5b9c0e6faaf0e1        3.336506    -0.079192   
2  8be5c854fd664bcb97fb543339f74770        3.212236     0.269894   
3  5543e4dc327359ffaf5b9c0e6faaf0e1        2.769522    -0.428278   
4  a73f82288988b79be490c6322f4c32ed       -0.663454     0.095351   

  flown_distance            tow  duration  MTOW(kg)  passengers  \
0      -0.630854   54748.000000 -0.573622 -0.316980   -0.222165   
1       3.093692  185441.000000  3.284415  2.347972    2.167263   
2       2.686801  230396.000000  3.179416  2.083337    2.013107   
3       2.530009  157615.000000  2.712471  2.052583    0.702775   
4      -0.646244   70318.447226 -0.653233  0.038224    0.240305   

   ROC_Initial_Climb(ft/min)  V2 (IAS)  
0                  -0.084663 -0.028796  
1                   1.182970  3.077931  
2                  -1.352296 -0.028796  
3                   0.422391  2.456586  
4                  -1.352296 -0.028796  

[5 rows x 23 columns]

## Categorical Encoding

In [ ]:
text_cols = norm_df.select_dtypes(include=['object']).columns
text_df = norm_df[text_cols]
for col in text_df:
  print(col, text_df[col].nunique())

callsign 10841
adep 453
name_adep 453
country_code_adep 98
ades 360
name_ades 360
country_code_ades 76
aircraft_type 28
wtc 2
airline 29


In [ ]:
def encode_categorical_features(df):
    categorical_col = [
        "adep",
        "country_code_adep",
        "ades",
        "country_code_ades",
        "aircraft_type",
        "airline",
    ]

    encoder = LabelEncoder()

    for col in categorical_col:
        df[col + "_encoded"] = encoder.fit_transform(df[col])

    df = df.drop(columns=categorical_col)

    oneHot_col = ["wtc"]
    df = pd.get_dummies(df, columns=oneHot_col)#, drop_first=True)


    df["wtc_M"] = df["wtc_M"].astype(int)
    df["wtc_H"] = df["wtc_H"].astype(int)

    return df
encoded_df = encode_categorical_features(norm_df)
encoded_df.head()

flight_id       date                          callsign          name_adep  \
0  248763780 2022-01-01  3840d84f25d3f5fcc0a1be3076bb4039    London Heathrow   
1  248760618 2022-01-01  f6f610e73002b8892a239a81321f7f1d          Barcelona   
2  248753824 2022-01-01  139670936660762c230ca92556ba842b  Stockholm Arlanda   
3  248753852 2022-01-01  509dc61bb54fbab0e5406067c95603e2             Zurich   
4  248755934 2022-01-01  d0610d000dcf26b1d7bba8103ecc393d             Dublin   

         name_ades      actual_offblock_time              arrival_time  \
0             Cork 2022-01-01 13:46:00+00:00 2022-01-01 15:04:56+00:00   
1            Miami 2022-01-01 09:55:00+00:00 2022-01-01 19:37:56+00:00   
2   Chicago O'Hare 2022-01-01 09:39:00+00:00 2022-01-01 19:08:13+00:00   
3     Philadelphia 2022-01-01 11:04:00+00:00 2022-01-01 19:32:13+00:00   
4  London Heathrow 2022-01-01 12:36:00+00:00 2022-01-01 13:44:32+00:00   

   flight_duration  taxiout_time  flown_distance  ...  \
0        -0.616852      0.793523       -0.630854  ...   
1         3.336506     -0.079192        3.093692  ...   
2         3.212236      0.269894        2.686801  ...   
3         2.769522     -0.428278        2.530009  ...   
4        -0.663454      0.095351       -0.646244  ...   

   ROC_Initial_Climb(ft/min)  V2 (IAS)  adep_encoded  \
0                  -0.084663 -0.028796            67   
1                   1.182970  3.077931           210   
2                  -1.352296 -0.028796           133   
3                   0.422391  2.456586           328   
4                  -1.352296 -0.028796            89   

   country_code_adep_encoded  ades_encoded  country_code_ades_encoded  \
0                         36            76                         32   
1                         32           159                         73   
2                         83           162                         73   
3                         19           163                         73   
4                         43            55                         25   

   aircraft_type_encoded  airline_encoded  wtc_H  wtc_M  
0                      3               20      0      1  
1                     17               10      1      0  
2                      6               18      1      0  
3                     20               10      1      0  
4                      1               20      0      1  

[5 rows x 24 columns]

## Feature Selection

In [ ]:
def drop_features(norm_df):
  drop_cols = [
            # "flight_id",
            "date",
            "callsign",
            "name_adep",
            "name_ades",
            "actual_offblock_time",
            "arrival_time",
        ]
  dropped_df = norm_df.drop(columns=drop_cols, errors='ignore')

  return dropped_df

drop_df = drop_features(encoded_df)
drop_df.head()

flight_id  flight_duration  taxiout_time  flown_distance            tow  \
0  248763780        -0.616852      0.793523       -0.630854   54748.000000   
1  248760618         3.336506     -0.079192        3.093692  185441.000000   
2  248753824         3.212236      0.269894        2.686801  230396.000000   
3  248753852         2.769522     -0.428278        2.530009  157615.000000   
4  248755934        -0.663454      0.095351       -0.646244   70318.447226   

   duration  MTOW(kg)  passengers  ROC_Initial_Climb(ft/min)  V2 (IAS)  \
0 -0.573622 -0.316980   -0.222165                  -0.084663 -0.028796   
1  3.284415  2.347972    2.167263                   1.182970  3.077931   
2  3.179416  2.083337    2.013107                  -1.352296 -0.028796   
3  2.712471  2.052583    0.702775                   0.422391  2.456586   
4 -0.653233  0.038224    0.240305                  -1.352296 -0.028796   

   adep_encoded  country_code_adep_encoded  ades_encoded  \
0            67                         36            76   
1           210                         32           159   
2           133                         83           162   
3           328                         19           163   
4            89                         43            55   

   country_code_ades_encoded  aircraft_type_encoded  airline_encoded  wtc_H  \
0                         32                      3               20      0   
1                         73                     17               10      1   
2                         73                      6               18      1   
3                         73                     20               10      1   
4                         25                      1               20      0   

   wtc_M  
0      1  
1      0  
2      0  
3      0  
4      1

In [ ]:
def feature_selection(
  X_train,
  y_train,
  X_test,
  k=15
):
  """Selects the best features from the training data and applies them to the test data."""

  selector = SelectKBest(score_func=f_regression, k=k)

  selector.fit(X_train, y_train)
  selected_features = X_train.columns[selector.get_support()]

  selected_features_df = pd.DataFrame(
      selected_features, columns=["Selected Features"]
  )

  feature_scores_df = pd.DataFrame(
      {
          "Feature": X_train.columns,
          "Score": selector.scores_,
          "p-value": selector.pvalues_,
      }
  )

  X_train_selected = selector.transform(X_train)
  X_test_selected = selector.transform(X_test)

  X_train_selected = pd.DataFrame(
      X_train_selected, columns=selected_features, index=X_train.index
  )
  X_test_selected = pd.DataFrame(
      X_test_selected, columns=selected_features, index=X_test.index
  )

  return X_train_selected, X_test_selected, selected_features_df, feature_scores_df

### Split the data by wtc

In [ ]:
def split_wtc(df):
  X = df.drop(['tow'], axis=1)
  y = df[['flight_id', 'tow']]

  X_wtc_M = X[X['wtc_M'] == 1].drop(["wtc_H", "wtc_M"], axis=1).reset_index(drop=True)
  X_wtc_H = X[X['wtc_H'] == 1].drop(["wtc_H", "wtc_M"], axis=1).reset_index(drop=True)

  y_wtc_M = y[y['flight_id'].isin(X_wtc_M.flight_id.unique())].drop('flight_id', axis=1).reset_index(drop=True)
  y_wtc_H = y[y['flight_id'].isin(X_wtc_H.flight_id.unique())].drop('flight_id', axis=1).reset_index(drop=True)

  X_wtc_M = X_wtc_M.drop('flight_id', axis=1).reset_index(drop=True)
  X_wtc_H = X_wtc_H.drop('flight_id', axis=1).reset_index(drop=True)

  return X_wtc_M, X_wtc_H, y_wtc_M, y_wtc_H

In [ ]:
if config.SPLIT_BY_WTC:
  X_wtc_M, X_wtc_H, y_wtc_M, y_wtc_H = split_wtc(drop_df)

  X_wtc_H_train, X_wtc_H_test, y_wtc_H_train, y_wtc_H_test = train_test_split(
    X_wtc_H, y_wtc_H, test_size=0.2, random_state=42
  )

  X_wtc_M_train, X_wtc_M_test, y_wtc_M_train, y_wtc_M_test = train_test_split(
    X_wtc_M, y_wtc_M, test_size=0.2, random_state=42
  )

  print("X_wtc_H_train shape:", X_wtc_H_train.shape)
  print("X_wtc_H_test shape:", X_wtc_H_test.shape)
  print("y_wtc_H_train shape:", y_wtc_H_train.shape)
  print("y_wtc_H_test shape:", y_wtc_H_test.shape)

  print("X_wtc_M_train shape:", X_wtc_M_train.shape)
  print("X_wtc_M_test shape:", X_wtc_M_test.shape)
  print("y_wtc_M_train shape:", y_wtc_M_train.shape)
  print("y_wtc_M_test shape:", y_wtc_M_test.shape)

  X_train_selected_H, X_test_selected_H, selected_features_df_H, feature_scores_df_H = feature_selection(X_wtc_H_train, y_wtc_H_train, X_wtc_H_test)
  X_train_selected_M, X_test_selected_M, selected_features_df_M, feature_scores_df_M = feature_selection(X_wtc_M_train, y_wtc_M_train, X_wtc_M_test)

  print("Selected Features for wtc_H:\n", selected_features_df_H)
  print("Feature Scores for wtc_H:\n", feature_scores_df_H)

  print("Selected Features for wtc_M:\n", selected_features_df_M)
  print("Feature Scores for wtc_M:\n", feature_scores_df_M)

### Split the data by mtow

In [ ]:
def split_by_mtow(df):
  """Splits the DataFrame into three ranges based on the 'MTOW(kg)' column."""
  df['MTOW_range'] = pd.qcut(df['MTOW(kg)'], q=3, labels=['Low', 'Medium', 'High'])
  X = df.drop(['tow', 'MTOW_range'], axis=1)
  y = df[['flight_id', 'tow']]

  X_low = X[df['MTOW_range'] == 'Low'].reset_index(drop=True)
  X_medium = X[df['MTOW_range'] == 'Medium'].reset_index(drop=True)
  X_high = X[df['MTOW_range'] == 'High'].reset_index(drop=True)

  y_low = y[y['flight_id'].isin(X_low.flight_id.unique())].drop('flight_id', axis=1).reset_index(drop=True)
  y_medium = y[y['flight_id'].isin(X_medium.flight_id.unique())].drop('flight_id', axis=1).reset_index(drop=True)
  y_high = y[y['flight_id'].isin(X_high.flight_id.unique())].drop('flight_id', axis=1).reset_index(drop=True)

  return X_low, X_medium, X_high, y_low, y_medium, y_high

In [ ]:
if config.SPLIT_BY_MTOW:
  X_low, X_medium, X_high, y_low, y_medium, y_high = split_by_mtow(drop_df)

  X_low_train, X_low_test, y_low_train, y_low_test = train_test_split(
    X_low, y_low, test_size=0.2, random_state=42
  )

  X_medium_train, X_medium_test, y_medium_train, y_medium_test = train_test_split(
    X_medium, y_medium, test_size=0.2, random_state=42
  )

  X_high_train, X_high_test, y_high_train, y_high_test = train_test_split(
    X_high, y_high, test_size=0.2, random_state=42
  )

  print("Low MTOW Train shape:", X_low_train.shape)
  print("Low MTOW Test shape:", X_low_test.shape)
  print("Low MTOW y Train shape:", y_low_train.shape)
  print("Low MTOW y Test shape:", y_low_test.shape)

  print("Medium MTOW Train shape:", X_medium_train.shape)
  print("Medium MTOW Test shape:", X_medium_test.shape)
  print("Medium MTOW y Train shape:", y_medium_train.shape)
  print("Medium MTOW y Test shape:", y_medium_test.shape)

  print("High MTOW Train shape:", X_high_train.shape)
  print("High MTOW Test shape:", X_high_test.shape)
  print("High MTOW y Train shape:", y_high_train.shape)
  print("High MTOW y Test shape:", y_high_test.shape)

  X_train_selected_low, X_test_selected_low, selected_features_df_low, feature_scores_df_low  = feature_selection(X_low_train, y_low_train, X_low_test)
  X_train_selected_medium, X_test_selected_medium, selected_features_df_medium, feature_scores_df_medium = feature_selection(X_medium_train, y_medium_train, X_medium_test)
  X_train_selected_high, X_test_selected_high, selected_features_df_high, feature_scores_df_high = feature_selection(X_high_train, y_high_train, X_high_test)

  print("Selected Features for Low MTOW:\n", selected_features_df_low)
  print("Selected Features for Medium MTOW:\n", selected_features_df_medium)
  print("Selected Features for High MTOW:\n", selected_features_df_high)

### Split the data by train test

In [ ]:
def split_train_test(df):
  X = df.drop(['tow'], axis=1)
  y = df[['tow']]
  X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
  return X_train, X_test, y_train, y_test


In [ ]:
if not config.SPLIT_BY_MTOW and not config.SPLIT_BY_WTC:
  X_train, X_test, y_train, y_test = split_train_test(drop_df)

# Modelling

## Find best model

In [ ]:
def select_best_model(
  X_train,
  y_train,
) -> Dict[str, any]:
  """Selects the best regression model using PyCaret's automated model selection with GPU acceleration."""

  train_data = pd.concat([X_train, y_train], axis=1)

  # Setup with GPU acceleration and other useful parameters
  reg = setup(
      data=train_data,
      target="tow",
      session_id=42,
      use_gpu=False,
      fold=3,
      remove_multicollinearity=True,  # Remove multicollinearity
      multicollinearity_threshold=0.95,  # Threshold for multicollinearity
      normalize=True,  # Normalize the data
      transformation=True,
      n_jobs=-1,

  )

  best_model = compare_models(
      n_select=1,
      sort="RMSE",
      fold=3,
      round=4,
      cross_validation=True,
      budget_time=600,
      turbo=False,
      errors='ignore'
  )

  best_model_name = best_model.__class__.__name__
  best_model_params = best_model.get_params()

  return {
      "model": best_model,
      "model_name": best_model_name,
      "params": best_model_params,
  }

In [ ]:
if config.FIND_BEST_MODEL:
  model_info = select_best_model(X_train_selected, y_train)
  model_info

## Train one model

### Catboost

In [ ]:
def train_catboost_model(X_train, y_train, X_test, y_test, model_name):
  model = CatBoostRegressor(random_state=42)

  param_grid = {
      'iterations': [1000, 2000],
      'learning_rate': [0.01, 0.1],
      'depth': [4, 6, 8]
  }

  grid_search = GridSearchCV(model, param_grid, scoring='neg_mean_squared_error', cv=3, verbose=100)
  grid_search.fit(X_train, y_train, eval_set=(X_test, y_test), early_stopping_rounds=50, verbose=100)

  best_model = grid_search.best_estimator_
  y_pred = best_model.predict(X_test)
  rmse = np.sqrt(mean_squared_error(y_test, y_pred))
  print(f"CatBoost Model ({model_name}) RMSE: {rmse}")
  print(f"Best Parameters: {grid_search.best_params_}")

  # Save the model to Google Drive
  joblib.dump(best_model, config.CATBOOST_MODEL_PATH_TEMPLATE.format(model_name))
  print(f"CatBoost model ({model_name}) saved to {config.CATBOOST_MODEL_PATH_TEMPLATE.format(model_name)}")

  feature_importance = pd.DataFrame({
      'feature': X_train.columns,
      'importance': best_model.feature_importances_
  }).sort_values('importance', ascending=False)

  print("\nTop 10 Most Important Features:")
  print(feature_importance.head(10))
  return y_pred

#### Train by wtc

In [ ]:
if config.SPLIT_BY_WTC and not config.USE_ENSEMBLE:
  print("Training CatBoost Model for wtc_H:")
  train_catboost_model(X_train_selected_H, y_wtc_H_train, X_test_selected_H, y_wtc_H_test, "wtc_H")

  print("\nTraining CatBoost Model for wtc_M:")
  train_catboost_model(X_train_selected_M, y_wtc_M_train, X_test_selected_M, y_wtc_M_test, "wtc_M")

### Train by MTOW

In [ ]:
if config.SPLIT_BY_MTOW and not config.USE_ENSEMBLE:
  print("Training CatBoost Model for Low MTOW:")
  train_catboost_model(X_train_selected_low, y_low_train, X_test_selected_low, y_low_test, "Low MTOW")

  print("\nTraining CatBoost Model for Medium MTOW:")
  train_catboost_model(X_train_selected_medium, y_medium_train, X_test_selected_medium, y_medium_test, "Medium MTOW")

  print("\nTraining CatBoost Model for High MTOW:")
  train_catboost_model(X_train_selected_high, y_high_train, X_test_selected_high, y_high_test, "High MTOW")

#### Train by train_test

In [ ]:
if not config.SPLIT_BY_MTOW and not config.SPLIT_BY_WTC:
  train_catboost_model(X_train, y_train, X_test, y_test, "Train Test Catboost")

### XGBoost

In [ ]:
def train_xgboost_model(X_train, y_train, X_test, y_test, model_name):
  model = XGBRegressor(random_state=42)

  param_grid = {
      'n_estimators': [1000, 2000],
      'learning_rate': [0.01, 0.1],
      'max_depth': [4, 6, 8]
  }

  grid_search = GridSearchCV(model, param_grid, scoring='neg_mean_squared_error', cv=3, verbose=100)
  grid_search.fit(X_train, y_train, eval_set=[(X_test, y_test)], verbose=100)

  best_model = grid_search.best_estimator_
  y_pred = best_model.predict(X_test)
  rmse = np.sqrt(mean_squared_error(y_test, y_pred))
  print(f"XGBoost Model ({model_name}) RMSE: {rmse}")
  print(f"Best Parameters: {grid_search.best_params_}")

  joblib.dump(best_model, config.XGBOOST_MODEL_PATH_TEMPLATE.format(model_name))
  print(f"XGBoost model ({model_name}) saved to {config.XGBOOST_MODEL_PATH_TEMPLATE.format(model_name)}")

  feature_importance = pd.DataFrame({
      'feature': X_train.columns,
      'importance': best_model.feature_importances_
  }).sort_values('importance', ascending=False)

  print("\nTop 10 Most Important Features:")
  print(feature_importance.head(10))
  return y_pred


#### Train by wtc

In [ ]:
if config.SPLIT_BY_WTC and not config.USE_ENSEMBLE:
  print("Training XGBoost Model for wtc_H:")
  train_xgboost_model(X_train_selected_H, y_wtc_H_train, X_test_selected_H, y_wtc_H_test, "wtc_H")
  print("\nTraining XGBoost Model for wtc_M:")
  train_xgboost_model(X_train_selected_M, y_wtc_M_train, X_test_selected_M, y_wtc_M_test, "wtc_M")

#### Train by MTOW

In [ ]:
if config.SPLIT_BY_MTOW and not config.USE_ENSEMBLE:
  print("Training XGBoost Model for Low MTOW:")
  train_xgboost_model(X_train_selected_low, y_low_train, X_test_selected_low, y_low_test, "Low MTOW")

  print("\nTraining XGBoost Model for Medium MTOW:")
  train_xgboost_model(X_train_selected_medium, y_medium_train, X_test_selected_medium, y_medium_test, "Medium MTOW")

  print("\nTraining XGBoost Model for High MTOW:")
  train_xgboost_model(X_train_selected_high, y_high_train, X_test_selected_high, y_high_test, "High MTOW")

#### Train by train_test

In [ ]:
if not config.SPLIT_BY_MTOW and not config.SPLIT_BY_WTC:
  train_catboost_model(X_train, y_train, X_test, y_test, "Train Test XGBoost")

## Ensemble Model

In [ ]:
def ensemble_models(X_train, y_train, X_test, y_test, model_name):
  y_pred_catboost = train_catboost_model(X_train, y_train, X_test, y_test, model_name)
  y_pred_xgboost = train_xgboost_model(X_train, y_train, X_test, y_test, model_name)

  y_pred_ensemble = (y_pred_catboost + y_pred_xgboost) / 2
  ensemble_rmse = np.sqrt(mean_squared_error(y_test, y_pred_ensemble))
  print(f"Ensemble Model ({model_name}) RMSE: {ensemble_rmse}")

  feature_importance = pd.DataFrame({
      'feature': X_train.columns,
  }).set_index('feature')

  feature_importance['catboost_importance'] = train_catboost_model(X_train, y_train, X_test, y_test, model_name)[1]
  feature_importance['xgboost_importance'] = train_xgboost_model(X_train, y_train, X_test, y_test, model_name)[1]
  feature_importance['average_importance'] = feature_importance.mean(axis=1)
  feature_importance = feature_importance.sort_values('average_importance', ascending=False)

  print("\nTop 10 Most Important Features (Ensemble):")
  print(feature_importance.head(10))

  return y_pred_ensemble

In [ ]:
if config.USE_ENSEMBLE:
  print("Training ensemble_models for Low MTOW:")
  ensemble_models(X_train_selected_low, y_low_train, X_test_selected_low, y_low_test, "low_mtow")

  print("\nTraining ensemble_models for Medium MTOW:")
  ensemble_models(X_train_selected_medium, y_medium_train, X_test_selected_medium, y_medium_test, "medium_mtow")

  print("\nTraining ensemble_models for High MTOW:")
  ensemble_models(X_train_selected_high, y_high_train, X_test_selected_high, y_high_test, "high_mtow")

# Predicting

In [ ]:
def load_catboost_model():
  model = joblib.load(config.CATBOOST_MODEL_PATH)
  print(f"Loaded CatBoost model from {config.CATBOOST_MODEL_PATH}")
  return model

def load_xgboost_model():
  model = joblib.load(config.XGBOOST_MODEL_PATH)
  print(f"Loaded XGBoost model from {config.XGBOOST_MODEL_PATH}")
  return model

def predict_with_catboost(X):
  model = load_catboost_model()
  return model.predict(X)

def predict_with_xgboost(X):
  model = load_xgboost_model()
  return model.predict(X)